---
## **Exercise: Recommendation System (Content Based Filtering)**

**Gunakan dataset anime.csv**

**1. Cosine Similarity**
- Seorang user telah menonton 'Kimi No Nawa'. Berikan rekomendasi anime menggunakan Cosine Similarity!


**2. Content based filtering for one user**
- Pilih 3 anime yang disukai user (bebas), contoh: 'Naruto', 'One Piece', 'Dragon Ball'
- Buat user feature vector
- Cari 10 rekomendasi anime untuk user


**3. Rekomendasikan masing-masing 10 anime untuk setiap user**

Buatlah:
- Item feature: anime_id, name, genre
- Buat user-item rating matrix di mana isinya adalah 4 user dan 4 anime yang sudah diberi rating oleh keempat user tersebut (buat secara random saja)
        
        Contoh:
        
        df_user_items = pd.DataFrame({
        'user': ['user 1', 'user 2', 'user 3', 'user 4'],
        951:     [9, 4, 6, 7],
        136:    [9, 7,  9, 7],
        235:    [7, 8,  9, 7],
        918:    [5, 9,  5, 7]
        })

            
- Buat item-feature matrix untuk semua anime dan pilih 4 anime yang sudah diberi rating di atas
- Buat user feature matrix dan user feature vector-nya
- Buat rekomendasi untuk anime yang belum ditonton
- Sort dan filtering 10 rekomendasi anime untuk tiap user

## **Import libraries**

In [81]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer

import warnings
warnings.filterwarnings('ignore')

pd.set_option('display.max_columns', None)

## **Load dataset**

In [82]:
df = pd.read_csv('anime.csv')
df

anime_id                                               name  \
0         32281                                     Kimi no Na wa.   
1          5114                   Fullmetal Alchemist: Brotherhood   
2         28977                                           Gintama°   
3          9253                                        Steins;Gate   
4          9969                                      Gintama&#039;   
...         ...                                                ...   
12289      9316       Toushindai My Lover: Minami tai Mecha-Minami   
12290      5543                                        Under World   
12291      5621                     Violence Gekiga David no Hoshi   
12292      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...   
12293     26081                   Yasuji no Pornorama: Yacchimae!!   

                                                   genre   type episodes  \
0                   Drama, Romance, School, Supernatural  Movie        1   
1      Action, Adventure, Drama, Fantasy, Magic, Mili...     TV       64   
2      Action, Comedy, Historical, Parody, Samurai, S...     TV       51   
3                                       Sci-Fi, Thriller     TV       24   
4      Action, Comedy, Historical, Parody, Samurai, S...     TV       51   
...                                                  ...    ...      ...   
12289                                             Hentai    OVA        1   
12290                                             Hentai    OVA        1   
12291                                             Hentai    OVA        4   
12292                                             Hentai    OVA        1   
12293                                             Hentai  Movie        1   

       rating  members  
0        9.37   200630  
1        9.26   793665  
2        9.25   114262  
3        9.17   673572  
4        9.16   151266  
...       ...      ...  
12289    4.15      211  
12290    4.28      183  
12291    4.88      219  
12292    4.98      175  
12293    5.46      142  

[12294 rows x 7 columns]

## **Preprocessing**

In [83]:
df = df.loc[:, ['anime_id', 'name', 'genre', 'rating']]
df

anime_id                                               name  \
0         32281                                     Kimi no Na wa.   
1          5114                   Fullmetal Alchemist: Brotherhood   
2         28977                                           Gintama°   
3          9253                                        Steins;Gate   
4          9969                                      Gintama&#039;   
...         ...                                                ...   
12289      9316       Toushindai My Lover: Minami tai Mecha-Minami   
12290      5543                                        Under World   
12291      5621                     Violence Gekiga David no Hoshi   
12292      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...   
12293     26081                   Yasuji no Pornorama: Yacchimae!!   

                                                   genre  rating  
0                   Drama, Romance, School, Supernatural    9.37  
1      Action, Adventure, Drama, Fantasy, Magic, Mili...    9.26  
2      Action, Comedy, Historical, Parody, Samurai, S...    9.25  
3                                       Sci-Fi, Thriller    9.17  
4      Action, Comedy, Historical, Parody, Samurai, S...    9.16  
...                                                  ...     ...  
12289                                             Hentai    4.15  
12290                                             Hentai    4.28  
12291                                             Hentai    4.88  
12292                                             Hentai    4.98  
12293                                             Hentai    5.46  

[12294 rows x 4 columns]

In [84]:
df.isna().sum()

anime_id      0
name          0
genre        62
rating      230
dtype: int64

In [85]:
df.shape

(12294, 4)

In [86]:
# drop missing values
df = df.dropna()
df.shape

(12017, 4)

In [87]:
# urutkan index kembali
df = df.reset_index(drop=True)
df

anime_id                                               name  \
0         32281                                     Kimi no Na wa.   
1          5114                   Fullmetal Alchemist: Brotherhood   
2         28977                                           Gintama°   
3          9253                                        Steins;Gate   
4          9969                                      Gintama&#039;   
...         ...                                                ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami   
12013      5543                                        Under World   
12014      5621                     Violence Gekiga David no Hoshi   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...   
12016     26081                   Yasuji no Pornorama: Yacchimae!!   

                                                   genre  rating  
0                   Drama, Romance, School, Supernatural    9.37  
1      Action, Adventure, Drama, Fantasy, Magic, Mili...    9.26  
2      Action, Comedy, Historical, Parody, Samurai, S...    9.25  
3                                       Sci-Fi, Thriller    9.17  
4      Action, Comedy, Historical, Parody, Samurai, S...    9.16  
...                                                  ...     ...  
12012                                             Hentai    4.15  
12013                                             Hentai    4.28  
12014                                             Hentai    4.88  
12015                                             Hentai    4.98  
12016                                             Hentai    5.46  

[12017 rows x 4 columns]

## **Create Item-Feature matrix**

In [88]:
# Generate item feature matrix
vect = CountVectorizer(tokenizer=lambda x:x.split(', '))

df_genre = vect.fit_transform(df['genre'])
df_genre = pd.DataFrame(df_genre.toarray(), columns=vect.get_feature_names())
df_genre

action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
0           0          0     0       0         0       0      1      0   
1           1          1     0       0         0       0      1      0   
2           1          0     0       1         0       0      0      0   
3           0          0     0       0         0       0      0      0   
4           1          0     0       1         0       0      0      0   
...       ...        ...   ...     ...       ...     ...    ...    ...   
12012       0          0     0       0         0       0      0      0   
12013       0          0     0       0         0       0      0      0   
12014       0          0     0       0         0       0      0      0   
12015       0          0     0       0         0       0      0      0   
12016       0          0     0       0         0       0      0      0   

       fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
0            0     0      0       0           0       0      0     0      0   
1            1     0      0       0           0       0      0     0      1   
2            0     0      0       0           1       0      0     0      0   
3            0     0      0       0           0       0      0     0      0   
4            0     0      0       0           1       0      0     0      0   
...        ...   ...    ...     ...         ...     ...    ...   ...    ...   
12012        0     0      0       1           0       0      0     0      0   
12013        0     0      0       1           0       0      0     0      0   
12014        0     0      0       1           0       0      0     0      0   
12015        0     0      0       1           0       0      0     0      0   
12016        0     0      0       1           0       0      0     0      0   

       martial arts  mecha  military  music  mystery  parody  police  \
0                 0      0         0      0        0       0       0   
1                 0      0         1      0        0       0       0   
2                 0      0         0      0        0       1       0   
3                 0      0         0      0        0       0       0   
4                 0      0         0      0        0       1       0   
...             ...    ...       ...    ...      ...     ...     ...   
12012             0      0         0      0        0       0       0   
12013             0      0         0      0        0       0       0   
12014             0      0         0      0        0       0       0   
12015             0      0         0      0        0       0       0   
12016             0      0         0      0        0       0       0   

       psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
0                  0        1        0       1       0       0       0   
1                  0        0        0       0       0       0       0   
2                  0        0        1       0       1       0       0   
3                  0        0        0       0       1       0       0   
4                  0        0        1       0       1       0       0   
...              ...      ...      ...     ...     ...     ...     ...   
12012              0        0        0       0       0       0       0   
12013              0        0        0       0       0       0       0   
12014              0        0        0       0       0       0       0   
12015              0        0        0       0       0       0       0   
12016              0        0        0       0       0       0       0   

       shoujo ai  shounen  shounen ai  slice of life  space  sports  \
0              0        0           0              0      0       0   
1              0        1           0              0      0       0   
2              0        1           0              0      0       0   
3              0        0           0              0      0       0   
4              0        1           0              0      0 

In [89]:
df_genre = pd.concat([df[['anime_id', 'name', 'rating']], df_genre], axis=1)
df_genre 

anime_id                                               name  rating  \
0         32281                                     Kimi no Na wa.    9.37   
1          5114                   Fullmetal Alchemist: Brotherhood    9.26   
2         28977                                           Gintama°    9.25   
3          9253                                        Steins;Gate    9.17   
4          9969                                      Gintama&#039;    9.16   
...         ...                                                ...     ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami    4.15   
12013      5543                                        Under World    4.28   
12014      5621                     Violence Gekiga David no Hoshi    4.88   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...    4.98   
12016     26081                   Yasuji no Pornorama: Yacchimae!!    5.46   

       action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
0           0          0     0       0         0       0      1      0   
1           1          1     0       0         0       0      1      0   
2           1          0     0       1         0       0      0      0   
3           0          0     0       0         0       0      0      0   
4           1          0     0       1         0       0      0      0   
...       ...        ...   ...     ...       ...     ...    ...    ...   
12012       0          0     0       0         0       0      0      0   
12013       0          0     0       0         0       0      0      0   
12014       0          0     0       0         0       0      0      0   
12015       0          0     0       0         0       0      0      0   
12016       0          0     0       0         0       0      0      0   

       fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
0            0     0      0       0           0       0      0     0      0   
1            1     0      0       0           0       0      0     0      1   
2            0     0      0       0           1       0      0     0      0   
3            0     0      0       0           0       0      0     0      0   
4            0     0      0       0           1       0      0     0      0   
...        ...   ...    ...     ...         ...     ...    ...   ...    ...   
12012        0     0      0       1           0       0      0     0      0   
12013        0     0      0       1           0       0      0     0      0   
12014        0     0      0       1           0       0      0     0      0   
12015        0     0      0       1           0       0      0     0      0   
12016        0     0      0       1           0       0      0     0      0   

       martial arts  mecha  military  music  mystery  parody  police  \
0                 0      0         0      0        0       0       0   
1                 0      0         1      0        0       0       0   
2                 0      0         0      0        0       1       0   
3                 0      0         0      0        0       0       0   
4                 0      0         0      0        0       1       0   
...             ...    ...       ...    ...      ...     ...     ...   
12012             0      0         0      0        0       0       0   
12013             0      0         0      0        0       0       0   
12014             0      0         0      0        0       0       0   
12015             0      0         0      0        0       0       0   
12016             0      0         0      0        0       0       0   

       psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
0                  0        1        0       1       0       0       0   
1                  0        0        0       0       0       0       0   
2                  0        0        1       0       1       0       0   
3                  0        0        0       0       1       0       0 

In [90]:
(vect.get_feature_names_out())

array(['action', 'adventure', 'cars', 'comedy', 'dementia', 'demons',
       'drama', 'ecchi', 'fantasy', 'game', 'harem', 'hentai',
       'historical', 'horror', 'josei', 'kids', 'magic', 'martial arts',
       'mecha', 'military', 'music', 'mystery', 'parody', 'police',
       'psychological', 'romance', 'samurai', 'school', 'sci-fi',
       'seinen', 'shoujo', 'shoujo ai', 'shounen', 'shounen ai',
       'slice of life', 'space', 'sports', 'super power', 'supernatural',
       'thriller', 'vampire', 'yaoi', 'yuri'], dtype=object)

---
# **1. Cosine Similarity**

In [91]:
from sklearn.metrics.pairwise import cosine_distances, cosine_similarity

In [92]:
# Anime yang sudah ditonton: Kimi No Na Wa
df_genre.iloc[:1, :]

anime_id            name  rating  action  adventure  cars  comedy  \
0     32281  Kimi no Na wa.    9.37       0          0     0       0   

   dementia  demons  drama  ecchi  fantasy  game  harem  hentai  historical  \
0         0       0      1      0        0     0      0       0           0   

   horror  josei  kids  magic  martial arts  mecha  military  music  mystery  \
0       0      0     0      0             0      0         0      0        0   

   parody  police  psychological  romance  samurai  school  sci-fi  seinen  \
0       0       0              0        1        0       1       0       0   

   shoujo  shoujo ai  shounen  shounen ai  slice of life  space  sports  \
0       0          0        0           0              0      0       0   

   super power  supernatural  thriller  vampire  yaoi  yuri  
0            0             1         0        0     0     0

In [93]:
# Item-Feature marix (1x43)
my_anime = df_genre.iloc[:1, 3:]
my_anime

action  adventure  cars  comedy  dementia  demons  drama  ecchi  fantasy  \
0       0          0     0       0         0       0      1      0        0   

   game  harem  hentai  historical  horror  josei  kids  magic  martial arts  \
0     0      0       0           0       0      0     0      0             0   

   mecha  military  music  mystery  parody  police  psychological  romance  \
0      0         0      0        0       0       0              0        1   

   samurai  school  sci-fi  seinen  shoujo  shoujo ai  shounen  shounen ai  \
0        0       1       0       0       0          0        0           0   

   slice of life  space  sports  super power  supernatural  thriller  vampire  \
0              0      0       0            0             1         0        0   

   yaoi  yuri  
0     0     0

In [94]:
# semua anime
all_anime = df_genre.iloc[: , 3:]
all_anime

action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
0           0          0     0       0         0       0      1      0   
1           1          1     0       0         0       0      1      0   
2           1          0     0       1         0       0      0      0   
3           0          0     0       0         0       0      0      0   
4           1          0     0       1         0       0      0      0   
...       ...        ...   ...     ...       ...     ...    ...    ...   
12012       0          0     0       0         0       0      0      0   
12013       0          0     0       0         0       0      0      0   
12014       0          0     0       0         0       0      0      0   
12015       0          0     0       0         0       0      0      0   
12016       0          0     0       0         0       0      0      0   

       fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
0            0     0      0       0           0       0      0     0      0   
1            1     0      0       0           0       0      0     0      1   
2            0     0      0       0           1       0      0     0      0   
3            0     0      0       0           0       0      0     0      0   
4            0     0      0       0           1       0      0     0      0   
...        ...   ...    ...     ...         ...     ...    ...   ...    ...   
12012        0     0      0       1           0       0      0     0      0   
12013        0     0      0       1           0       0      0     0      0   
12014        0     0      0       1           0       0      0     0      0   
12015        0     0      0       1           0       0      0     0      0   
12016        0     0      0       1           0       0      0     0      0   

       martial arts  mecha  military  music  mystery  parody  police  \
0                 0      0         0      0        0       0       0   
1                 0      0         1      0        0       0       0   
2                 0      0         0      0        0       1       0   
3                 0      0         0      0        0       0       0   
4                 0      0         0      0        0       1       0   
...             ...    ...       ...    ...      ...     ...     ...   
12012             0      0         0      0        0       0       0   
12013             0      0         0      0        0       0       0   
12014             0      0         0      0        0       0       0   
12015             0      0         0      0        0       0       0   
12016             0      0         0      0        0       0       0   

       psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
0                  0        1        0       1       0       0       0   
1                  0        0        0       0       0       0       0   
2                  0        0        1       0       1       0       0   
3                  0        0        0       0       1       0       0   
4                  0        0        1       0       1       0       0   
...              ...      ...      ...     ...     ...     ...     ...   
12012              0        0        0       0       0       0       0   
12013              0        0        0       0       0       0       0   
12014              0        0        0       0       0       0       0   
12015              0        0        0       0       0       0       0   
12016              0        0        0       0       0       0       0   

       shoujo ai  shounen  shounen ai  slice of life  space  sports  \
0              0        0           0              0      0       0   
1              0        1           0              0      0       0   
2              0        1           0              0      0       0   
3              0        0           0              0      0       0   
4              0        1           0              0      0 

In [95]:
# Menghitung cosine_similarity antara my_anime dengan tiap anime
cosine_score = cosine_similarity(my_anime, all_anime)
cosine_score

array([[1.        , 0.18898224, 0.        , ..., 0.        , 0.        ,
        0.        ]])

In [96]:
df_cos = df_genre[['anime_id', 'name','rating']].copy()

df_cos['cosine'] = cosine_score.reshape(-1)
df_cos

anime_id                                               name  rating  \
0         32281                                     Kimi no Na wa.    9.37   
1          5114                   Fullmetal Alchemist: Brotherhood    9.26   
2         28977                                           Gintama°    9.25   
3          9253                                        Steins;Gate    9.17   
4          9969                                      Gintama&#039;    9.16   
...         ...                                                ...     ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami    4.15   
12013      5543                                        Under World    4.28   
12014      5621                     Violence Gekiga David no Hoshi    4.88   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...    4.98   
12016     26081                   Yasuji no Pornorama: Yacchimae!!    5.46   

         cosine  
0      1.000000  
1      0.188982  
2      0.000000  
3      0.000000  
4      0.000000  
...         ...  
12012  0.000000  
12013  0.000000  
12014  0.000000  
12015  0.000000  
12016  0.000000  

[12017 rows x 4 columns]

In [97]:
# 10 Anime yang paling mirip genrenya dengan 'Kimi No Nawa' 
df_cos.sort_values('cosine', ascending=False).head(11)[['name', 'cosine']]

name    cosine
0                            Kimi no Na wa.  1.000000
5803            Wind: A Breath of Heart OVA  1.000000
6391           Wind: A Breath of Heart (TV)  1.000000
1111  Aura: Maryuuin Kouga Saigo no Tatakai  0.894427
1631                    Kimikiss Pure Rouge  0.866025
5231                     To Heart 2 Special  0.866025
4512                           Touka Gettan  0.866025
2300             Koi to Senkyo to Chocolate  0.866025
1494                               Harmonie  0.866025
1201         Angel Beats!: Another Epilogue  0.866025
1907                       Myself; Yourself  0.866025

---
# **2. Content Based Filtering for One User**

## Select 3 anime you have been watched or like

Memilih 3 anime (items) yang paling disukai. 
Recommender System nanti akan memberikan rekomendasi anime yang paling serupa dengan 3 anime yang paling disukai ini.

In [98]:
# Lihat-lihat nama anime dan genre
search = 'chibi'
  
result = df['name'].apply(lambda x: x.lower()).str.contains(search) 
df[result].head(10)

anime_id                                               name  \
744        951                                  Chibi Maruko-chan   
1889      3203                            Chibi Maruko-chan Movie   
2030      6149                           Chibi Maruko-chan (1995)   
2975      9348          Chibi Maruko-chan: Watashi no Suki na Uta   
3013       596                                   Chobits: Chibits   
3858     11457                                        Chibi☆Devi!   
4827      5449                 Chibi Kero: Kerobouru no Himitsu!?   
5318      1158              Geobreeders: File-X Chibi Neko Dakkan   
6057      2830                       Chibikko Remi to Meiken Kapi   
6145      5783  Koisuru Tenshi Angelique: Chibi Character Adve...   

                                         genre  rating  
744              Comedy, Shoujo, Slice of Life    7.86  
1889                    Comedy, School, Shoujo    7.41  
2030       Comedy, Kids, School, Slice of Life    7.37  
2975                     Comedy, Slice of Life    7.11  
3013                           Comedy, Romance    7.10  
3858             Fantasy, Shoujo, Supernatural    6.86  
4827                                    Comedy    6.62  
5318  Adventure, Comedy, Shounen, Supernatural    6.49  
6057           Adventure, Drama, Slice of Life    6.26  
6145                         Adventure, Comedy    6.24

In [99]:
# list anime yg sudah ditonton

list_watched = ['Doraemon', 'Crayon Shin-chan', 'Chibi Maruko-chan']

## Item-feature matrix with rating

In [100]:
# Buat item-feature matrix (anime yang sudah ditonton)

df_choice = df_genre[df_genre['name'].isin(list_watched)]
# df_choice = df_choice.drop(columns='cosine')
df_choice 

anime_id               name  rating  action  adventure  cars  comedy  \
744        951  Chibi Maruko-chan    7.86       0          0     0       1   
991        966   Crayon Shin-chan    7.73       0          0     0       1   
1587       501           Doraemon    7.49       0          1     0       1   

      dementia  demons  drama  ecchi  fantasy  game  harem  hentai  \
744          0       0      0      0        0     0      0       0   
991          0       0      0      1        0     0      0       0   
1587         0       0      0      0        1     0      0       0   

      historical  horror  josei  kids  magic  martial arts  mecha  military  \
744            0       0      0     0      0             0      0         0   
991            0       0      0     1      0             0      0         0   
1587           0       0      0     1      0             0      0         0   

      music  mystery  parody  police  psychological  romance  samurai  school  \
744       0        0       0       0              0        0        0       0   
991       0        0       0       0              0        0        0       1   
1587      0        0       0       0              0        0        0       0   

      sci-fi  seinen  shoujo  shoujo ai  shounen  shounen ai  slice of life  \
744        0       0       1          0        0           0              1   
991        0       0       0          0        1           0              1   
1587       0       0       0          0        1           0              0   

      space  sports  super power  supernatural  thriller  vampire  yaoi  yuri  
744       0       0            0             0         0        0     0     0  
991       0       0            0             0         0        0     0     0  
1587      0       0            0             0         0        0     0     0

In [101]:
# jumlah genre yg terdapat pada ketiga anime di atas 
df_choice.loc[:, 'action':].sum(axis=1)

744     3
991     6
1587    5
dtype: int64

In [102]:
# rating tiap anime
df_choice['rating']

744     7.86
991     7.73
1587    7.49
Name: rating, dtype: float64

In [103]:
# item feature matix with rating --> kalikan dataframe dengan series berisi score
df_item_feature_rating = df_choice.loc[:, 'action':].multiply(df_choice['rating'], axis=0)
df_item_feature_rating

action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
744      0.0       0.00   0.0    7.86       0.0     0.0    0.0   0.00   
991      0.0       0.00   0.0    7.73       0.0     0.0    0.0   7.73   
1587     0.0       7.49   0.0    7.49       0.0     0.0    0.0   0.00   

      fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
744      0.00   0.0    0.0     0.0         0.0     0.0    0.0  0.00    0.0   
991      0.00   0.0    0.0     0.0         0.0     0.0    0.0  7.73    0.0   
1587     7.49   0.0    0.0     0.0         0.0     0.0    0.0  7.49    0.0   

      martial arts  mecha  military  music  mystery  parody  police  \
744            0.0    0.0       0.0    0.0      0.0     0.0     0.0   
991            0.0    0.0       0.0    0.0      0.0     0.0     0.0   
1587           0.0    0.0       0.0    0.0      0.0     0.0     0.0   

      psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
744             0.0      0.0      0.0    0.00     0.0     0.0    7.86   
991             0.0      0.0      0.0    7.73     0.0     0.0    0.00   
1587            0.0      0.0      0.0    0.00     0.0     0.0    0.00   

      shoujo ai  shounen  shounen ai  slice of life  space  sports  \
744         0.0     0.00         0.0           7.86    0.0     0.0   
991         0.0     7.73         0.0           7.73    0.0     0.0   
1587        0.0     7.49         0.0           0.00    0.0     0.0   

      super power  supernatural  thriller  vampire  yaoi  yuri  
744           0.0           0.0       0.0      0.0   0.0   0.0  
991           0.0           0.0       0.0      0.0   0.0   0.0  
1587          0.0           0.0       0.0      0.0   0.0   0.0

## Calculating user feature vector

In [104]:
# jumlahkan nilai pada masing-masing kolom/genre (content)
df_item_feature_rating.sum()

action            0.00
adventure         7.49
cars              0.00
comedy           23.08
dementia          0.00
demons            0.00
drama             0.00
ecchi             7.73
fantasy           7.49
game              0.00
harem             0.00
hentai            0.00
historical        0.00
horror            0.00
josei             0.00
kids             15.22
magic             0.00
martial arts      0.00
mecha             0.00
military          0.00
music             0.00
mystery           0.00
parody            0.00
police            0.00
psychological     0.00
romance           0.00
samurai           0.00
school            7.73
sci-fi            0.00
seinen            0.00
shoujo            7.86
shoujo ai         0.00
shounen          15.22
shounen ai        0.00
slice of life    15.59
space             0.00
sports            0.00
super power       0.00
supernatural      0.00
thriller          0.00
vampire           0.00
yaoi              0.00
yuri              0.00
dtype: floa

In [105]:
# normalisasi nilainya agar totalnya menjadi 100%
user_feature_vector = df_item_feature_rating.sum() / df_item_feature_rating.sum().sum()
user_feature_vector

action           0.000000
adventure        0.069733
cars             0.000000
comedy           0.214878
dementia         0.000000
demons           0.000000
drama            0.000000
ecchi            0.071967
fantasy          0.069733
game             0.000000
harem            0.000000
hentai           0.000000
historical       0.000000
horror           0.000000
josei            0.000000
kids             0.141700
magic            0.000000
martial arts     0.000000
mecha            0.000000
military         0.000000
music            0.000000
mystery          0.000000
parody           0.000000
police           0.000000
psychological    0.000000
romance          0.000000
samurai          0.000000
school           0.071967
sci-fi           0.000000
seinen           0.000000
shoujo           0.073178
shoujo ai        0.000000
shounen          0.141700
shounen ai       0.000000
slice of life    0.145145
space            0.000000
sports           0.000000
super power      0.000000
supernatural

In [163]:
# preferensi atau Top genre paling disukai oleh user berikut:
user_feature_vector.sort_values(ascending=False).head(15)

comedy           0.157895
shounen          0.157895
action           0.105263
adventure        0.105263
historical       0.052632
super power      0.052632
slice of life    0.052632
shoujo           0.052632
sci-fi           0.052632
samurai          0.052632
police           0.052632
parody           0.052632
mystery          0.052632
horror                0.0
josei                 0.0
dtype: object

## Create recommendation

Kalikan hasil user feature vector dengan semua list anime, sehingga nanti tiap judul anime, genre-nya memiliki nilai user feature vector berdasarkan anime yang sudah ditonton.

In [107]:
df_genre.shape

(12017, 46)

In [108]:
# Dataframe anime yang belum ditonton
df_recommend = df_genre.loc[~df_genre['name'].isin([list_watched])]
# df_recommend = df_recommend.drop(columns='cosine')
df_recommend = df_recommend.reset_index(drop=True)
df_recommend

anime_id                                               name  rating  \
0         32281                                     Kimi no Na wa.    9.37   
1          5114                   Fullmetal Alchemist: Brotherhood    9.26   
2         28977                                           Gintama°    9.25   
3          9253                                        Steins;Gate    9.17   
4          9969                                      Gintama&#039;    9.16   
...         ...                                                ...     ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami    4.15   
12013      5543                                        Under World    4.28   
12014      5621                     Violence Gekiga David no Hoshi    4.88   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...    4.98   
12016     26081                   Yasuji no Pornorama: Yacchimae!!    5.46   

       action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
0           0          0     0       0         0       0      1      0   
1           1          1     0       0         0       0      1      0   
2           1          0     0       1         0       0      0      0   
3           0          0     0       0         0       0      0      0   
4           1          0     0       1         0       0      0      0   
...       ...        ...   ...     ...       ...     ...    ...    ...   
12012       0          0     0       0         0       0      0      0   
12013       0          0     0       0         0       0      0      0   
12014       0          0     0       0         0       0      0      0   
12015       0          0     0       0         0       0      0      0   
12016       0          0     0       0         0       0      0      0   

       fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
0            0     0      0       0           0       0      0     0      0   
1            1     0      0       0           0       0      0     0      1   
2            0     0      0       0           1       0      0     0      0   
3            0     0      0       0           0       0      0     0      0   
4            0     0      0       0           1       0      0     0      0   
...        ...   ...    ...     ...         ...     ...    ...   ...    ...   
12012        0     0      0       1           0       0      0     0      0   
12013        0     0      0       1           0       0      0     0      0   
12014        0     0      0       1           0       0      0     0      0   
12015        0     0      0       1           0       0      0     0      0   
12016        0     0      0       1           0       0      0     0      0   

       martial arts  mecha  military  music  mystery  parody  police  \
0                 0      0         0      0        0       0       0   
1                 0      0         1      0        0       0       0   
2                 0      0         0      0        0       1       0   
3                 0      0         0      0        0       0       0   
4                 0      0         0      0        0       1       0   
...             ...    ...       ...    ...      ...     ...     ...   
12012             0      0         0      0        0       0       0   
12013             0      0         0      0        0       0       0   
12014             0      0         0      0        0       0       0   
12015             0      0         0      0        0       0       0   
12016             0      0         0      0        0       0       0   

       psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
0                  0        1        0       1       0       0       0   
1                  0        0        0       0       0       0       0   
2                  0        0        1       0       1       0       0   
3                  0        0        0       0       1       0       0 

In [109]:
df_recommend.loc[:, 'action':]

action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
0           0          0     0       0         0       0      1      0   
1           1          1     0       0         0       0      1      0   
2           1          0     0       1         0       0      0      0   
3           0          0     0       0         0       0      0      0   
4           1          0     0       1         0       0      0      0   
...       ...        ...   ...     ...       ...     ...    ...    ...   
12012       0          0     0       0         0       0      0      0   
12013       0          0     0       0         0       0      0      0   
12014       0          0     0       0         0       0      0      0   
12015       0          0     0       0         0       0      0      0   
12016       0          0     0       0         0       0      0      0   

       fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
0            0     0      0       0           0       0      0     0      0   
1            1     0      0       0           0       0      0     0      1   
2            0     0      0       0           1       0      0     0      0   
3            0     0      0       0           0       0      0     0      0   
4            0     0      0       0           1       0      0     0      0   
...        ...   ...    ...     ...         ...     ...    ...   ...    ...   
12012        0     0      0       1           0       0      0     0      0   
12013        0     0      0       1           0       0      0     0      0   
12014        0     0      0       1           0       0      0     0      0   
12015        0     0      0       1           0       0      0     0      0   
12016        0     0      0       1           0       0      0     0      0   

       martial arts  mecha  military  music  mystery  parody  police  \
0                 0      0         0      0        0       0       0   
1                 0      0         1      0        0       0       0   
2                 0      0         0      0        0       1       0   
3                 0      0         0      0        0       0       0   
4                 0      0         0      0        0       1       0   
...             ...    ...       ...    ...      ...     ...     ...   
12012             0      0         0      0        0       0       0   
12013             0      0         0      0        0       0       0   
12014             0      0         0      0        0       0       0   
12015             0      0         0      0        0       0       0   
12016             0      0         0      0        0       0       0   

       psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
0                  0        1        0       1       0       0       0   
1                  0        0        0       0       0       0       0   
2                  0        0        1       0       1       0       0   
3                  0        0        0       0       1       0       0   
4                  0        0        1       0       1       0       0   
...              ...      ...      ...     ...     ...     ...     ...   
12012              0        0        0       0       0       0       0   
12013              0        0        0       0       0       0       0   
12014              0        0        0       0       0       0       0   
12015              0        0        0       0       0       0       0   
12016              0        0        0       0       0       0       0   

       shoujo ai  shounen  shounen ai  slice of life  space  sports  \
0              0        0           0              0      0       0   
1              0        1           0              0      0       0   
2              0        1           0              0      0       0   
3              0        0           0              0      0       0   
4              0        1           0              0      0 

In [110]:
user_feature_vector

action           0.000000
adventure        0.069733
cars             0.000000
comedy           0.214878
dementia         0.000000
demons           0.000000
drama            0.000000
ecchi            0.071967
fantasy          0.069733
game             0.000000
harem            0.000000
hentai           0.000000
historical       0.000000
horror           0.000000
josei            0.000000
kids             0.141700
magic            0.000000
martial arts     0.000000
mecha            0.000000
military         0.000000
music            0.000000
mystery          0.000000
parody           0.000000
police           0.000000
psychological    0.000000
romance          0.000000
samurai          0.000000
school           0.071967
sci-fi           0.000000
seinen           0.000000
shoujo           0.073178
shoujo ai        0.000000
shounen          0.141700
shounen ai       0.000000
slice of life    0.145145
space            0.000000
sports           0.000000
super power      0.000000
supernatural

In [111]:
# kalikan dataframe film yg belum ditonton dengan series user_feature_vector
df_scoring = df_recommend.loc[:, 'action':].multiply(user_feature_vector, axis=1)
df_scoring

# prediksi score yang akan diberikan oleh user pada film yang belum ditonton

action  adventure  cars    comedy  dementia  demons  drama  ecchi  \
0         0.0   0.000000   0.0  0.000000       0.0     0.0    0.0    0.0   
1         0.0   0.069733   0.0  0.000000       0.0     0.0    0.0    0.0   
2         0.0   0.000000   0.0  0.214878       0.0     0.0    0.0    0.0   
3         0.0   0.000000   0.0  0.000000       0.0     0.0    0.0    0.0   
4         0.0   0.000000   0.0  0.214878       0.0     0.0    0.0    0.0   
...       ...        ...   ...       ...       ...     ...    ...    ...   
12012     0.0   0.000000   0.0  0.000000       0.0     0.0    0.0    0.0   
12013     0.0   0.000000   0.0  0.000000       0.0     0.0    0.0    0.0   
12014     0.0   0.000000   0.0  0.000000       0.0     0.0    0.0    0.0   
12015     0.0   0.000000   0.0  0.000000       0.0     0.0    0.0    0.0   
12016     0.0   0.000000   0.0  0.000000       0.0     0.0    0.0    0.0   

        fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
0      0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
1      0.069733   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
2      0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
3      0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
4      0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
...         ...   ...    ...     ...         ...     ...    ...   ...    ...   
12012  0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
12013  0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
12014  0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
12015  0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   
12016  0.000000   0.0    0.0     0.0         0.0     0.0    0.0   0.0    0.0   

       martial arts  mecha  military  music  mystery  parody  police  \
0               0.0    0.0       0.0    0.0      0.0     0.0     0.0   
1               0.0    0.0       0.0    0.0      0.0     0.0     0.0   
2               0.0    0.0       0.0    0.0      0.0     0.0     0.0   
3               0.0    0.0       0.0    0.0      0.0     0.0     0.0   
4               0.0    0.0       0.0    0.0      0.0     0.0     0.0   
...             ...    ...       ...    ...      ...     ...     ...   
12012           0.0    0.0       0.0    0.0      0.0     0.0     0.0   
12013           0.0    0.0       0.0    0.0      0.0     0.0     0.0   
12014           0.0    0.0       0.0    0.0      0.0     0.0     0.0   
12015           0.0    0.0       0.0    0.0      0.0     0.0     0.0   
12016           0.0    0.0       0.0    0.0      0.0     0.0     0.0   

       psychological  romance  samurai    school  sci-fi  seinen  shoujo  \
0                0.0      0.0      0.0  0.071967     0.0     0.0     0.0   
1                0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
2                0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
3                0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
4                0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
...              ...      ...      ...       ...     ...     ...     ...   
12012            0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
12013            0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
12014            0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
12015            0.0      0.0      0.0  0.000000     0.0     0.0     0.0   
12016            0.0      0.0      0.0  0.000000     0.0     0.0     0.0   

       shoujo ai  shounen  shounen ai  slice of life  space  sports  \
0            0.0   0.0000         0.0            0.0    0.0     0.0   
1            0.0   0.1417         0.0            0.0    0.0     0.0   
2            0.0   0.1417         0.0            0.0    0.0     0.0   
3            0.0   0.0000         0.0            0.0    0.0     0.0   


In [112]:
df_scoring.insert(0, 'name', df_recommend['name'])
df_scoring

name  action  adventure  \
0                                         Kimi no Na wa.     0.0   0.000000   
1                       Fullmetal Alchemist: Brotherhood     0.0   0.069733   
2                                               Gintama°     0.0   0.000000   
3                                            Steins;Gate     0.0   0.000000   
4                                          Gintama&#039;     0.0   0.000000   
...                                                  ...     ...        ...   
12012       Toushindai My Lover: Minami tai Mecha-Minami     0.0   0.000000   
12013                                        Under World     0.0   0.000000   
12014                     Violence Gekiga David no Hoshi     0.0   0.000000   
12015  Violence Gekiga Shin David no Hoshi: Inma Dens...     0.0   0.000000   
12016                   Yasuji no Pornorama: Yacchimae!!     0.0   0.000000   

       cars    comedy  dementia  demons  drama  ecchi   fantasy  game  harem  \
0       0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
1       0.0  0.000000       0.0     0.0    0.0    0.0  0.069733   0.0    0.0   
2       0.0  0.214878       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
3       0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
4       0.0  0.214878       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
...     ...       ...       ...     ...    ...    ...       ...   ...    ...   
12012   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12013   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12014   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12015   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12016   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   

       hentai  historical  horror  josei  kids  magic  martial arts  mecha  \
0         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
1         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
2         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
3         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
4         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
...       ...         ...     ...    ...   ...    ...           ...    ...   
12012     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12013     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12014     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12015     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12016     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   

       military  music  mystery  parody  police  psychological  romance  \
0           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
1           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
2           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
3           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
4           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
...         ...    ...      ...     ...     ...            ...      ...   
12012       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12013       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12014       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12015       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12016       0.0    0.0      0.0     0.0     0.0            0.0      0.0   

       samurai    school  sci-fi  seinen  shoujo  shoujo ai  shounen  \
0          0.0  0.071967     0.0     0.0     0.0        0.0   0.0000   
1          0.0  0.000000     0.0     0.0     0.0        0.0   0.1417   
2          0.0  0.000000     0.0     0.0     0.0        0.0   0.1417   
3          0.0  

## Create predicted score column

In [113]:
# total score semua genre dari tiap film

df_scoring.iloc[:, 1:].sum(axis=1)

0        0.071967
1        0.281166
2        0.356578
3        0.000000
4        0.356578
           ...   
12012    0.000000
12013    0.000000
12014    0.000000
12015    0.000000
12016    0.000000
Length: 12017, dtype: float64

In [114]:
# 'predicted score' : total score semua genre dari tiap film

df_scoring['predicted score'] = df_scoring.iloc[:, 1:].sum(axis=1)
df_scoring

name  action  adventure  \
0                                         Kimi no Na wa.     0.0   0.000000   
1                       Fullmetal Alchemist: Brotherhood     0.0   0.069733   
2                                               Gintama°     0.0   0.000000   
3                                            Steins;Gate     0.0   0.000000   
4                                          Gintama&#039;     0.0   0.000000   
...                                                  ...     ...        ...   
12012       Toushindai My Lover: Minami tai Mecha-Minami     0.0   0.000000   
12013                                        Under World     0.0   0.000000   
12014                     Violence Gekiga David no Hoshi     0.0   0.000000   
12015  Violence Gekiga Shin David no Hoshi: Inma Dens...     0.0   0.000000   
12016                   Yasuji no Pornorama: Yacchimae!!     0.0   0.000000   

       cars    comedy  dementia  demons  drama  ecchi   fantasy  game  harem  \
0       0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
1       0.0  0.000000       0.0     0.0    0.0    0.0  0.069733   0.0    0.0   
2       0.0  0.214878       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
3       0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
4       0.0  0.214878       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
...     ...       ...       ...     ...    ...    ...       ...   ...    ...   
12012   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12013   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12014   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12015   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   
12016   0.0  0.000000       0.0     0.0    0.0    0.0  0.000000   0.0    0.0   

       hentai  historical  horror  josei  kids  magic  martial arts  mecha  \
0         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
1         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
2         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
3         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
4         0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
...       ...         ...     ...    ...   ...    ...           ...    ...   
12012     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12013     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12014     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12015     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   
12016     0.0         0.0     0.0    0.0   0.0    0.0           0.0    0.0   

       military  music  mystery  parody  police  psychological  romance  \
0           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
1           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
2           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
3           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
4           0.0    0.0      0.0     0.0     0.0            0.0      0.0   
...         ...    ...      ...     ...     ...            ...      ...   
12012       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12013       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12014       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12015       0.0    0.0      0.0     0.0     0.0            0.0      0.0   
12016       0.0    0.0      0.0     0.0     0.0            0.0      0.0   

       samurai    school  sci-fi  seinen  shoujo  shoujo ai  shounen  \
0          0.0  0.071967     0.0     0.0     0.0        0.0   0.0000   
1          0.0  0.000000     0.0     0.0     0.0        0.0   0.1417   
2          0.0  0.000000     0.0     0.0     0.0        0.0   0.1417   
3          0.0  

In [115]:
# Inilah 20 anime yang akan direkomendasikan kepada si User
top20 = df_scoring[['name', 'predicted score']].sort_values('predicted score', ascending=False).head(20)
top20

name  predicted score
3516  Crayon Shin-chan Movie 07: Bakuhatsu! Onsen Wa...         0.787357
3787  Crayon Shin-chan Movie 14: Densetsu wo Yobu Od...         0.787357
3896  Crayon Shin-chan Movie 13: Densetsu wo Yobu Bu...         0.787357
4231  Crayon Shin-chan Movie 16: Chou Arashi wo Yobu...         0.787357
864   Crayon Shin-chan Movie 09: Arashi wo Yobu Mour...         0.787357
2743      Crayon Shin-chan Movie 03: Unkokusai no Yabou         0.787357
2832  Crayon Shin-chan Movie 02: Buriburi Oukoku no ...         0.787357
2325  Crayon Shin-chan Movie 05: Ankoku Tamatama Dai...         0.787357
2437  Crayon Shin-chan Movie 04: Henderland no Daibo...         0.787357
2001  Crayon Shin-chan Movie 18: Chou Jikuu! Arashi ...         0.787357
2544  Crayon Shin-chan Movie 11: Arashi wo Yobu Eiko...         0.787357
3606  Crayon Shin-chan Movie 17: Otakebe! Kasukabe Y...         0.787357
3128  Crayon Shin-chan Movie 06: Dengeki! Buta no Hi...         0.787357
3127  Crayon Shin-chan Movie 01: Action Kamen vs. Ha...         0.787357
2601   Crayon Shin-chan Movie 08: Arashi wo Yobu Jungle         0.787357
2577  Crayon Shin-chan Movie 12: Arashi wo Yobu! Yuu...         0.787357
991                                    Crayon Shin-chan         0.787357
2961         Ochame na Futago: Claire Gakuin Monogatari         0.646867
4362                                            Kanokon         0.645657
5915                                    Asagiri no Miko         0.643422

In [116]:
list_watched

['Doraemon', 'Crayon Shin-chan', 'Chibi Maruko-chan']

### **Interpretasi**

Jadi, berdasarkan 3 pilihan anime, yaitu 'Doraemon', 'Crayon Shin-chan', 'Chibi Maruko-chan', 20 rekomendasi anime teratas (berdasarkan predicted score-nya) tercantum pada dataframe di atas, yang mana hasilnya kebanyakan adalah varian atau episode lain dari Crayon Shin-Chan.

### **All Process in Function**

In [117]:
list_anime = list_watched

def beri_rekomendasi(list_anime):

    # Create genre dataframe
    df = pd.read_csv('anime.csv')
    df = df.loc[:, ['anime_id', 'name', 'genre', 'rating']].dropna().reset_index(drop=True)

    # ==============================================================================
    # Generate item feature matrix
    vect = CountVectorizer(tokenizer=lambda x:x.split(', '))

    df_genre = vect.fit_transform(df['genre'])
    df_genre = pd.DataFrame(df_genre.toarray(), columns=vect.get_feature_names())
    df_genre = pd.concat([df[['anime_id', 'name', 'rating']], df_genre], axis=1)

    # ==============================================================================
    # Buat item-feature matrix (anime yang sudah ditonton)
    df_choice = df_genre[df_genre['name'].isin(list_anime)]
    df_choice

    # Buat item-feature matrix with (kalikan dataframe dengan series berisi score)
    df_item_feature_rating = df_choice.loc[:, 'action':].multiply(df_choice['rating'], axis=0)
    df_item_feature_rating

    # ==============================================================================
    # User Feature Vector
    user_feature_vector = df_item_feature_rating.sum() / df_item_feature_rating.sum().sum()
    user_feature_vector

    # ==============================================================================
    # Buat rekomendasi untuk anime yg belum ditonton

    # Dataframe anime yang belum ditonton
    df_recommend = df_genre.loc[~df_genre['name'].isin([list_anime])]
    df_recommend = df_recommend.reset_index(drop=True)
    df_recommend

    # prediksi score yang akan diberikan oleh user pada film yang belum ditonton
    # kalikan dataframe film yg belum ditonton dengan series user_feature_vector
    df_scoring = df_recommend.loc[:, 'action':].multiply(user_feature_vector, axis=1)
    df_scoring.insert(0, 'name', df_recommend['name'])
    df_scoring

    # 'predicted score' : total score semua genre dari tiap film
    df_scoring['predicted score'] = df_scoring.iloc[:, 1:].sum(axis=1)
    df_scoring

    # Top 20 anime yg paling disukai oleh si User
    top20 = df_scoring[['name', 'predicted score']].sort_values('predicted score', ascending=False).head(20)
    
    return top20

In [118]:
# gunakan function yg telah dibuat

list_watched = ['Doraemon', 'Crayon Shin-chan', 'Chibi Maruko-chan']

beri_rekomendasi(list_watched)

name  predicted score
3516  Crayon Shin-chan Movie 07: Bakuhatsu! Onsen Wa...         0.787357
3787  Crayon Shin-chan Movie 14: Densetsu wo Yobu Od...         0.787357
3896  Crayon Shin-chan Movie 13: Densetsu wo Yobu Bu...         0.787357
4231  Crayon Shin-chan Movie 16: Chou Arashi wo Yobu...         0.787357
864   Crayon Shin-chan Movie 09: Arashi wo Yobu Mour...         0.787357
2743      Crayon Shin-chan Movie 03: Unkokusai no Yabou         0.787357
2832  Crayon Shin-chan Movie 02: Buriburi Oukoku no ...         0.787357
2325  Crayon Shin-chan Movie 05: Ankoku Tamatama Dai...         0.787357
2437  Crayon Shin-chan Movie 04: Henderland no Daibo...         0.787357
2001  Crayon Shin-chan Movie 18: Chou Jikuu! Arashi ...         0.787357
2544  Crayon Shin-chan Movie 11: Arashi wo Yobu Eiko...         0.787357
3606  Crayon Shin-chan Movie 17: Otakebe! Kasukabe Y...         0.787357
3128  Crayon Shin-chan Movie 06: Dengeki! Buta no Hi...         0.787357
3127  Crayon Shin-chan Movie 01: Action Kamen vs. Ha...         0.787357
2601   Crayon Shin-chan Movie 08: Arashi wo Yobu Jungle         0.787357
2577  Crayon Shin-chan Movie 12: Arashi wo Yobu! Yuu...         0.787357
991                                    Crayon Shin-chan         0.787357
2961         Ochame na Futago: Claire Gakuin Monogatari         0.646867
4362                                            Kanokon         0.645657
5915                                    Asagiri no Miko         0.643422

---
# **3. Content Based Filtering for Multiple Users**

**Rekomendasikan masing-masing 10 anime untuk setiap user**

Buatlah:
- Item feature: anime_id, name, genre
- Buat user-item rating matrix di mana isinya adalah 4 user dan 4 anime yang sudah diberi rating oleh keempat user tersebut (buat secara random saja)
        
        Contoh:
        
        df_user_items = pd.DataFrame({
        'user': ['user 1', 'user 2', 'user 3', 'user 4'],
        951:     [9, 4, 6, 7],
        136:    [9, 7,  9, 7],
        235:    [7, 8,  9, 7],
        918:    [5, 9,  5, 7]
        })

            
- Buat item-feature matrix untuk semua anime dan pilih 4 anime yang sudah diberi rating di atas
- Buat user feature matrix dan user feature vector-nya
- Buat rekomendasi untuk anime yang belum ditonton
- Sort dan filtering 10 rekomendasi anime untuk tiap user

In [119]:
# Kalau mau cari nama anime yang mengandung kata tertentu
search = 'Hunter x Hunter'
  
result = df['name'].str.contains(search) 
df[result] 

anime_id                                     name  \
6        11061                   Hunter x Hunter (2011)   
112        136                          Hunter x Hunter   
145        137                      Hunter x Hunter OVA   
146        139      Hunter x Hunter: Greed Island Final   
202        138            Hunter x Hunter: Greed Island   
1974     13271     Hunter x Hunter Movie: Phantom Rouge   
2046     10189                    Hunter x Hunter Pilot   
2108     19951  Hunter x Hunter Movie: The Last Mission   

                                        genre  rating  
6     Action, Adventure, Shounen, Super Power    9.13  
112   Action, Adventure, Shounen, Super Power    8.48  
145   Action, Adventure, Shounen, Super Power    8.41  
146   Action, Adventure, Shounen, Super Power    8.41  
202   Action, Adventure, Shounen, Super Power    8.33  
1974  Action, Adventure, Shounen, Super Power    7.39  
2046  Action, Adventure, Shounen, Super Power    7.37  
2108  Action, Adventure, Shounen, Super Power    7.35

In [120]:
# Kalau mau cari genre anime yang mengandung kata tertentu
search = 'Super Power'
  
result = df['genre'].str.contains(search) 
df[result].head(30)

anime_id                                               name  \
6       11061                             Hunter x Hunter (2011)   
13       2904                 Code Geass: Hangyaku no Lelouch R2   
19       1575                    Code Geass: Hangyaku no Lelouch   
23      30276                                      One Punch Man   
55       4565       Tengen Toppa Gurren Lagann Movie: Lagann-hen   
74         21                                          One Piece   
86      16498                                 Shingeki no Kyojin   
112       136                                    Hunter x Hunter   
145       137                                Hunter x Hunter OVA   
146       139                Hunter x Hunter: Greed Island Final   
175      1604                             Katekyo Hitman Reborn!   
178     31964                              Boku no Hero Academia   
182      9130      Saint Seiya: The Lost Canvas - Meiou Shinwa 2   
194     10153  Mahou Shoujo Lyrical Nanoha: The Movie 2nd A&#...   
202       138                      Hunter x Hunter: Greed Island   
206       813                                      Dragon Ball Z   
231     19123  One Piece: Episode of Merry - Mou Hitori no Na...   
241     15323  One Piece: Episode of Nami - Koukaishi no Nami...   
251      2025              Darker than Black: Kuro no Keiyakusha   
271      6171        Saint Seiya: The Lost Canvas - Meiou Shinwa   
281     18679                                       Kill la Kill   
333      2952        Final Fantasy VII: Advent Children Complete   
346       223                                        Dragon Ball   
352      8740             One Piece Film: Strong World Episode 0   
355     16049                          Toaru Kagaku no Railgun S   
400      9941                                  Tiger &amp; Bunny   
416        77               Mahou Shoujo Lyrical Nanoha A&#039;s   
420      7338       Darker than Black: Kuro no Keiyakusha Gaiden   
447      6582                    Tentai Senshi Sunred 2nd Season   
480      4985         Mahou Shoujo Lyrical Nanoha: The Movie 1st   

                                                 genre  rating  
6              Action, Adventure, Shounen, Super Power    9.13  
13   Action, Drama, Mecha, Military, Sci-Fi, Super ...    8.98  
19   Action, Mecha, Military, School, Sci-Fi, Super...    8.83  
23   Action, Comedy, Parody, Sci-Fi, Seinen, Super ...    8.82  
55           Action, Mecha, Sci-Fi, Space, Super Power    8.64  
74   Action, Adventure, Comedy, Drama, Fantasy, Sho...    8.58  
86        Action, Drama, Fantasy, Shounen, Super Power    8.54  
112            Action, Adventure, Shounen, Super Power    8.48  
145            Action, Adventure, Shounen, Super Power    8.41  
146            Action, Adventure, Shounen, Super Power    8.41  
175               Action, Comedy, Shounen, Super Power    8.37  
178       Action, Comedy, School, Shounen, Super Power    8.36  
182  Action, Adventure, Martial Arts, Shounen, Supe...    8.36  
194          Action, Comedy, Drama, Magic, Super Power    8.34  
202            Action, Adventure, Shounen, Super Power    8.33  
206  Action, Adventure, Comedy, Fantasy, Martial Ar...    8.32  
231  Action, Adventure, Comedy, Drama, Fantasy, Sho...    8.29  
241  Action, Adventure, Comedy, Drama, Fantasy, Sho...    8.27  
251               Action, Mystery, Sci-Fi, Super Power    8.25  
271  Action, Adventure, Martial Arts, Shounen, Supe...    8.24  
281                Action, Comedy, School, Super Power    8.23  
333                       Action, Fantasy, Super Power    8.17  
346  Adventure, Comedy, Fantasy, Martial Arts, Shou...    8.16  
352  Action, Adventure, Comedy, Fantasy, Shounen, S...    8.16  
355                        Action, Sci-Fi, Super Power    8.16  
400               Action, Comedy, Mystery, Super Power    8.12  
416          Action, Comedy, Drama, Magic, Super Power    8.10  
420               Action, Mystery, Sci-Fi, Super Power    8.09  
447        

In [121]:
df[df['anime_id'] == 11061]

anime_id                    name                                    genre  \
6     11061  Hunter x Hunter (2011)  Action, Adventure, Shounen, Super Power   

   rating  
6    9.13

## Create a copy of df
Kita mulai 

In [122]:
df_multiple = df.copy()
df_multiple

anime_id                                               name  \
0         32281                                     Kimi no Na wa.   
1          5114                   Fullmetal Alchemist: Brotherhood   
2         28977                                           Gintama°   
3          9253                                        Steins;Gate   
4          9969                                      Gintama&#039;   
...         ...                                                ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami   
12013      5543                                        Under World   
12014      5621                     Violence Gekiga David no Hoshi   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...   
12016     26081                   Yasuji no Pornorama: Yacchimae!!   

                                                   genre  rating  
0                   Drama, Romance, School, Supernatural    9.37  
1      Action, Adventure, Drama, Fantasy, Magic, Mili...    9.26  
2      Action, Comedy, Historical, Parody, Samurai, S...    9.25  
3                                       Sci-Fi, Thriller    9.17  
4      Action, Comedy, Historical, Parody, Samurai, S...    9.16  
...                                                  ...     ...  
12012                                             Hentai    4.15  
12013                                             Hentai    4.28  
12014                                             Hentai    4.88  
12015                                             Hentai    4.98  
12016                                             Hentai    5.46  

[12017 rows x 4 columns]

## Choose only anime_id, name, genre columns and drop missing values
Kolom yang diperlukan

In [123]:
df_multiple = df_multiple[['anime_id', 'name', 'genre']].dropna().reset_index(drop=True)
df_multiple

anime_id                                               name  \
0         32281                                     Kimi no Na wa.   
1          5114                   Fullmetal Alchemist: Brotherhood   
2         28977                                           Gintama°   
3          9253                                        Steins;Gate   
4          9969                                      Gintama&#039;   
...         ...                                                ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami   
12013      5543                                        Under World   
12014      5621                     Violence Gekiga David no Hoshi   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...   
12016     26081                   Yasuji no Pornorama: Yacchimae!!   

                                                   genre  
0                   Drama, Romance, School, Supernatural  
1      Action, Adventure, Drama, Fantasy, Magic, Mili...  
2      Action, Comedy, Historical, Parody, Samurai, S...  
3                                       Sci-Fi, Thriller  
4      Action, Comedy, Historical, Parody, Samurai, S...  
...                                                  ...  
12012                                             Hentai  
12013                                             Hentai  
12014                                             Hentai  
12015                                             Hentai  
12016                                             Hentai  

[12017 rows x 3 columns]

## Create User-Item Rating matrix
Buat dataframe berisi 4 user dengan 4 anime yang (anggap saja) sudah ditonton dan diberi rating oleh masing masing user.

In [124]:
df_user_items = pd.DataFrame({
    'user': ['user 1', 'user 2', 'user 3', 'user 4'],
    951:     [9, 4, 6, 7],
    136:    [9, 7,  9, 7],
    235:    [7, 8,  9, 7],
    918:    [5, 9,  5, 7]
})

df_user_items

user  951  136  235  918
0  user 1    9    9    7    5
1  user 2    4    7    8    9
2  user 3    6    9    9    5
3  user 4    7    7    7    7

In [125]:
# Kalau mau lihat nama anime dari anime yg punya anime_id: 951, 136, 235, 918
df_multiple[df_multiple['anime_id'].isin(df_user_items.columns)]

anime_id               name  \
12        918            Gintama   
112       136    Hunter x Hunter   
252       235    Detective Conan   
744       951  Chibi Maruko-chan   

                                                 genre  
12   Action, Comedy, Historical, Parody, Samurai, S...  
112            Action, Adventure, Shounen, Super Power  
252        Adventure, Comedy, Mystery, Police, Shounen  
744                      Comedy, Shoujo, Slice of Life

## Create Item-Feature matrix
Matix berisi nama anime dan genrenya

In [126]:
vect = CountVectorizer(tokenizer=lambda x:x.split(', '))

df_genre = vect.fit_transform(df_multiple['genre'])
df_genre = pd.DataFrame(df_genre.toarray(), columns=vect.get_feature_names())
df_genre = pd.concat([df_multiple[['anime_id', 'name']], df_genre], axis=1)
df_genre 

anime_id                                               name  action  \
0         32281                                     Kimi no Na wa.       0   
1          5114                   Fullmetal Alchemist: Brotherhood       1   
2         28977                                           Gintama°       1   
3          9253                                        Steins;Gate       0   
4          9969                                      Gintama&#039;       1   
...         ...                                                ...     ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami       0   
12013      5543                                        Under World       0   
12014      5621                     Violence Gekiga David no Hoshi       0   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...       0   
12016     26081                   Yasuji no Pornorama: Yacchimae!!       0   

       adventure  cars  comedy  dementia  demons  drama  ecchi  fantasy  game  \
0              0     0       0         0       0      1      0        0     0   
1              1     0       0         0       0      1      0        1     0   
2              0     0       1         0       0      0      0        0     0   
3              0     0       0         0       0      0      0        0     0   
4              0     0       1         0       0      0      0        0     0   
...          ...   ...     ...       ...     ...    ...    ...      ...   ...   
12012          0     0       0         0       0      0      0        0     0   
12013          0     0       0         0       0      0      0        0     0   
12014          0     0       0         0       0      0      0        0     0   
12015          0     0       0         0       0      0      0        0     0   
12016          0     0       0         0       0      0      0        0     0   

       harem  hentai  historical  horror  josei  kids  magic  martial arts  \
0          0       0           0       0      0     0      0             0   
1          0       0           0       0      0     0      1             0   
2          0       0           1       0      0     0      0             0   
3          0       0           0       0      0     0      0             0   
4          0       0           1       0      0     0      0             0   
...      ...     ...         ...     ...    ...   ...    ...           ...   
12012      0       1           0       0      0     0      0             0   
12013      0       1           0       0      0     0      0             0   
12014      0       1           0       0      0     0      0             0   
12015      0       1           0       0      0     0      0             0   
12016      0       1           0       0      0     0      0             0   

       mecha  military  music  mystery  parody  police  psychological  \
0          0         0      0        0       0       0              0   
1          0         1      0        0       0       0              0   
2          0         0      0        0       1       0              0   
3          0         0      0        0       0       0              0   
4          0         0      0        0       1       0              0   
...      ...       ...    ...      ...     ...     ...            ...   
12012      0         0      0        0       0       0              0   
12013      0         0      0        0       0       0              0   
12014      0         0      0        0       0       0              0   
12015      0         0      0        0       0       0              0   
12016      0         0      0        0       0       0              0   

       romance  samurai  school  sci-fi  seinen  shoujo  shoujo ai  shounen  \
0            1        0       1       0       0       0          0        0   
1            0        0       0       0       0       0          0        1   
2            0        1       0       1       

In [127]:
df_user_items.columns[1:]

Index([951, 136, 235, 918], dtype='object')

In [128]:
# Item-Feature matrix untuk anime yang sudah ditonton
df_item_feature = df_genre.loc[df_genre['anime_id'].isin(df_user_items.columns[1:])]
df_item_feature

anime_id               name  action  adventure  cars  comedy  dementia  \
12        918            Gintama       1          0     0       1         0   
112       136    Hunter x Hunter       1          1     0       0         0   
252       235    Detective Conan       0          1     0       1         0   
744       951  Chibi Maruko-chan       0          0     0       1         0   

     demons  drama  ecchi  fantasy  game  harem  hentai  historical  horror  \
12        0      0      0        0     0      0       0           1       0   
112       0      0      0        0     0      0       0           0       0   
252       0      0      0        0     0      0       0           0       0   
744       0      0      0        0     0      0       0           0       0   

     josei  kids  magic  martial arts  mecha  military  music  mystery  \
12       0     0      0             0      0         0      0        0   
112      0     0      0             0      0         0      0        0   
252      0     0      0             0      0         0      0        1   
744      0     0      0             0      0         0      0        0   

     parody  police  psychological  romance  samurai  school  sci-fi  seinen  \
12        1       0              0        0        1       0       1       0   
112       0       0              0        0        0       0       0       0   
252       0       1              0        0        0       0       0       0   
744       0       0              0        0        0       0       0       0   

     shoujo  shoujo ai  shounen  shounen ai  slice of life  space  sports  \
12        0          0        1           0              0      0       0   
112       0          0        1           0              0      0       0   
252       0          0        1           0              0      0       0   
744       1          0        0           0              1      0       0   

     super power  supernatural  thriller  vampire  yaoi  yuri  
12             0             0         0        0     0     0  
112            1             0         0        0     0     0  
252            0             0         0        0     0     0  
744            0             0         0        0     0     0

In [129]:
# Kita samakan urutan anime_id di df_user_items (user item matrix) dan df_item_feature (item feature matrix)

# awalnya seperti ini
df_item_feature = df_item_feature.set_index('anime_id')
df_item_feature


name  action  adventure  cars  comedy  dementia  \
anime_id                                                                 
918                 Gintama       1          0     0       1         0   
136         Hunter x Hunter       1          1     0       0         0   
235         Detective Conan       0          1     0       1         0   
951       Chibi Maruko-chan       0          0     0       1         0   

          demons  drama  ecchi  fantasy  game  harem  hentai  historical  \
anime_id                                                                   
918            0      0      0        0     0      0       0           1   
136            0      0      0        0     0      0       0           0   
235            0      0      0        0     0      0       0           0   
951            0      0      0        0     0      0       0           0   

          horror  josei  kids  magic  martial arts  mecha  military  music  \
anime_id                                                                     
918            0      0     0      0             0      0         0      0   
136            0      0     0      0             0      0         0      0   
235            0      0     0      0             0      0         0      0   
951            0      0     0      0             0      0         0      0   

          mystery  parody  police  psychological  romance  samurai  school  \
anime_id                                                                     
918             0       1       0              0        0        1       0   
136             0       0       0              0        0        0       0   
235             1       0       1              0        0        0       0   
951             0       0       0              0        0        0       0   

          sci-fi  seinen  shoujo  shoujo ai  shounen  shounen ai  \
anime_id                                                           
918            1       0       0          0        1           0   
136            0       0       0          0        1           0   
235            0       0       0          0        1           0   
951            0       0       1          0        0           0   

          slice of life  space  sports  super power  supernatural  thriller  \
anime_id                                                                      
918                   0      0       0            0             0         0   
136                   0      0       0            1             0         0   
235                   0      0       0            0             0         0   
951                   1      0       0            0             0         0   

          vampire  yaoi  yuri  
anime_id                       
918             0     0     0  
136             0     0     0  
235             0     0     0  
951             0     0     0

In [130]:
df_item_feature = df_item_feature.loc[list(df_user_items.columns[1:]), :].reset_index()
df_item_feature

# sekarang nama anime sudah sesuai dengan urutan di df_user_items

anime_id               name  action  adventure  cars  comedy  dementia  \
0       951  Chibi Maruko-chan       0          0     0       1         0   
1       136    Hunter x Hunter       1          1     0       0         0   
2       235    Detective Conan       0          1     0       1         0   
3       918            Gintama       1          0     0       1         0   

   demons  drama  ecchi  fantasy  game  harem  hentai  historical  horror  \
0       0      0      0        0     0      0       0           0       0   
1       0      0      0        0     0      0       0           0       0   
2       0      0      0        0     0      0       0           0       0   
3       0      0      0        0     0      0       0           1       0   

   josei  kids  magic  martial arts  mecha  military  music  mystery  parody  \
0      0     0      0             0      0         0      0        0       0   
1      0     0      0             0      0         0      0        0       0   
2      0     0      0             0      0         0      0        1       0   
3      0     0      0             0      0         0      0        0       1   

   police  psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
0       0              0        0        0       0       0       0       1   
1       0              0        0        0       0       0       0       0   
2       1              0        0        0       0       0       0       0   
3       0              0        0        1       0       1       0       0   

   shoujo ai  shounen  shounen ai  slice of life  space  sports  super power  \
0          0        0           0              1      0       0            0   
1          0        1           0              0      0       0            1   
2          0        1           0              0      0       0            0   
3          0        1           0              0      0       0            0   

   supernatural  thriller  vampire  yaoi  yuri  
0             0         0        0     0     0  
1             0         0        0     0     0  
2             0         0        0     0     0  
3             0         0        0     0     0

## Create user feature vector

User Feature Vector menunjukkan preferensi dari masing masing user terhadap genre-genre tertentu

In [131]:
# anime yg mau diprediksi
list(df_user_items.columns[1:])

[951, 136, 235, 918]

In [132]:
# Item Feature matrix

df_item_feature = df_item_feature.set_index('anime_id')
df_item_feature

name  action  adventure  cars  comedy  dementia  \
anime_id                                                                 
951       Chibi Maruko-chan       0          0     0       1         0   
136         Hunter x Hunter       1          1     0       0         0   
235         Detective Conan       0          1     0       1         0   
918                 Gintama       1          0     0       1         0   

          demons  drama  ecchi  fantasy  game  harem  hentai  historical  \
anime_id                                                                   
951            0      0      0        0     0      0       0           0   
136            0      0      0        0     0      0       0           0   
235            0      0      0        0     0      0       0           0   
918            0      0      0        0     0      0       0           1   

          horror  josei  kids  magic  martial arts  mecha  military  music  \
anime_id                                                                     
951            0      0     0      0             0      0         0      0   
136            0      0     0      0             0      0         0      0   
235            0      0     0      0             0      0         0      0   
918            0      0     0      0             0      0         0      0   

          mystery  parody  police  psychological  romance  samurai  school  \
anime_id                                                                     
951             0       0       0              0        0        0       0   
136             0       0       0              0        0        0       0   
235             1       0       1              0        0        0       0   
918             0       1       0              0        0        1       0   

          sci-fi  seinen  shoujo  shoujo ai  shounen  shounen ai  \
anime_id                                                           
951            0       0       1          0        0           0   
136            0       0       0          0        1           0   
235            0       0       0          0        1           0   
918            1       0       0          0        1           0   

          slice of life  space  sports  super power  supernatural  thriller  \
anime_id                                                                      
951                   1      0       0            0             0         0   
136                   0      0       0            1             0         0   
235                   0      0       0            0             0         0   
918                   0      0       0            0             0         0   

          vampire  yaoi  yuri  
anime_id                       
951             0     0     0  
136             0     0     0  
235             0     0     0  
918             0     0     0

In [133]:
# Item Feature matrix (anime sudah sesuai urutan seperti di df_user_items)

df_item_feature.loc[list(df_user_items.columns[1:]), :]

name  action  adventure  cars  comedy  dementia  \
anime_id                                                                 
951       Chibi Maruko-chan       0          0     0       1         0   
136         Hunter x Hunter       1          1     0       0         0   
235         Detective Conan       0          1     0       1         0   
918                 Gintama       1          0     0       1         0   

          demons  drama  ecchi  fantasy  game  harem  hentai  historical  \
anime_id                                                                   
951            0      0      0        0     0      0       0           0   
136            0      0      0        0     0      0       0           0   
235            0      0      0        0     0      0       0           0   
918            0      0      0        0     0      0       0           1   

          horror  josei  kids  magic  martial arts  mecha  military  music  \
anime_id                                                                     
951            0      0     0      0             0      0         0      0   
136            0      0     0      0             0      0         0      0   
235            0      0     0      0             0      0         0      0   
918            0      0     0      0             0      0         0      0   

          mystery  parody  police  psychological  romance  samurai  school  \
anime_id                                                                     
951             0       0       0              0        0        0       0   
136             0       0       0              0        0        0       0   
235             1       0       1              0        0        0       0   
918             0       1       0              0        0        1       0   

          sci-fi  seinen  shoujo  shoujo ai  shounen  shounen ai  \
anime_id                                                           
951            0       0       1          0        0           0   
136            0       0       0          0        1           0   
235            0       0       0          0        1           0   
918            1       0       0          0        1           0   

          slice of life  space  sports  super power  supernatural  thriller  \
anime_id                                                                      
951                   1      0       0            0             0         0   
136                   0      0       0            1             0         0   
235                   0      0       0            0             0         0   
918                   0      0       0            0             0         0   

          vampire  yaoi  yuri  
anime_id                       
951             0     0     0  
136             0     0     0  
235             0     0     0  
918             0     0     0

**Coba hitung user_feature_vector untuk User 1 dulu**

In [134]:
df_item_feature.loc[list(df_user_items.columns[1:]), 'action':'yuri']

action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
anime_id                                                                    
951            0          0     0       1         0       0      0      0   
136            1          1     0       0         0       0      0      0   
235            0          1     0       1         0       0      0      0   
918            1          0     0       1         0       0      0      0   

          fantasy  game  harem  hentai  historical  horror  josei  kids  \
anime_id                                                                  
951             0     0      0       0           0       0      0     0   
136             0     0      0       0           0       0      0     0   
235             0     0      0       0           0       0      0     0   
918             0     0      0       0           1       0      0     0   

          magic  martial arts  mecha  military  music  mystery  parody  \
anime_id                                                                 
951           0             0      0         0      0        0       0   
136           0             0      0         0      0        0       0   
235           0             0      0         0      0        1       0   
918           0             0      0         0      0        0       1   

          police  psychological  romance  samurai  school  sci-fi  seinen  \
anime_id                                                                    
951            0              0        0        0       0       0       0   
136            0              0        0        0       0       0       0   
235            1              0        0        0       0       0       0   
918            0              0        0        1       0       1       0   

          shoujo  shoujo ai  shounen  shounen ai  slice of life  space  \
anime_id                                                                 
951            1          0        0           0              1      0   
136            0          0        1           0              0      0   
235            0          0        1           0              0      0   
918            0          0        1           0              0      0   

          sports  super power  supernatural  thriller  vampire  yaoi  yuri  
anime_id                                                                    
951            0            0             0         0        0     0     0  
136            0            1             0         0        0     0     0  
235            0            0             0         0        0     0     0  
918            0            0             0         0        0     0     0

In [135]:
df_user_items

user  951  136  235  918
0  user 1    9    9    7    5
1  user 2    4    7    8    9
2  user 3    6    9    9    5
3  user 4    7    7    7    7

In [136]:
df_user_items.iloc[0, 1:]

951    9
136    9
235    7
918    5
Name: 0, dtype: object

In [137]:
df_item_feature_rating = df_item_feature.loc[list(df_user_items.columns[1:]), 'action':'yuri'].multiply(df_user_items.iloc[0, 1:], axis=0)
df_item_feature_rating

action adventure cars comedy dementia demons drama ecchi fantasy  \
anime_id                                                                    
951           0         0    0      9        0      0     0     0       0   
136           9         9    0      0        0      0     0     0       0   
235           0         7    0      7        0      0     0     0       0   
918           5         0    0      5        0      0     0     0       0   

         game harem hentai historical horror josei kids magic martial arts  \
anime_id                                                                     
951         0     0      0          0      0     0    0     0            0   
136         0     0      0          0      0     0    0     0            0   
235         0     0      0          0      0     0    0     0            0   
918         0     0      0          5      0     0    0     0            0   

         mecha military music mystery parody police psychological romance  \
anime_id                                                                    
951          0        0     0       0      0      0             0       0   
136          0        0     0       0      0      0             0       0   
235          0        0     0       7      0      7             0       0   
918          0        0     0       0      5      0             0       0   

         samurai school sci-fi seinen shoujo shoujo ai shounen shounen ai  \
anime_id                                                                    
951            0      0      0      0      9         0       0          0   
136            0      0      0      0      0         0       9          0   
235            0      0      0      0      0         0       7          0   
918            5      0      5      0      0         0       5          0   

         slice of life space sports super power supernatural thriller vampire  \
anime_id                                                                        
951                  9     0      0           0            0        0       0   
136                  0     0      0           9            0        0       0   
235                  0     0      0           0            0        0       0   
918                  0     0      0           0            0        0       0   

         yaoi yuri  
anime_id            
951         0    0  
136         0    0  
235         0    0  
918         0    0

In [138]:
df_item_feature_rating.sum()

action           14
adventure        16
cars              0
comedy           21
dementia          0
demons            0
drama             0
ecchi             0
fantasy           0
game              0
harem             0
hentai            0
historical        5
horror            0
josei             0
kids              0
magic             0
martial arts      0
mecha             0
military          0
music             0
mystery           7
parody            5
police            7
psychological     0
romance           0
samurai           5
school            0
sci-fi            5
seinen            0
shoujo            9
shoujo ai         0
shounen          21
shounen ai        0
slice of life     9
space             0
sports            0
super power       9
supernatural      0
thriller          0
vampire           0
yaoi              0
yuri              0
dtype: object

In [139]:
user_feature_vector = df_item_feature_rating.sum() / df_item_feature_rating.sum().sum()
user_feature_vector

action           0.105263
adventure        0.120301
cars                  0.0
comedy           0.157895
dementia              0.0
demons                0.0
drama                 0.0
ecchi                 0.0
fantasy               0.0
game                  0.0
harem                 0.0
hentai                0.0
historical       0.037594
horror                0.0
josei                 0.0
kids                  0.0
magic                 0.0
martial arts          0.0
mecha                 0.0
military              0.0
music                 0.0
mystery          0.052632
parody           0.037594
police           0.052632
psychological         0.0
romance               0.0
samurai          0.037594
school                0.0
sci-fi           0.037594
seinen                0.0
shoujo           0.067669
shoujo ai             0.0
shounen          0.157895
shounen ai            0.0
slice of life    0.067669
space                 0.0
sports                0.0
super power      0.067669
supernatural

In [140]:
len(user_feature_vector.values)

43

In [141]:
user_feature_vector.values

array([0.10526315789473684, 0.12030075187969924, 0.0, 0.15789473684210525,
       0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.03759398496240601, 0.0,
       0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.05263157894736842,
       0.03759398496240601, 0.05263157894736842, 0.0, 0.0,
       0.03759398496240601, 0.0, 0.03759398496240601, 0.0,
       0.06766917293233082, 0.0, 0.15789473684210525, 0.0,
       0.06766917293233082, 0.0, 0.0, 0.06766917293233082, 0.0, 0.0, 0.0,
       0.0, 0.0], dtype=object)

In [142]:
len(df_item_feature_rating.columns)

43

In [143]:
df_item_feature.columns[1:]

Index(['action', 'adventure', 'cars', 'comedy', 'dementia', 'demons', 'drama',
       'ecchi', 'fantasy', 'game', 'harem', 'hentai', 'historical', 'horror',
       'josei', 'kids', 'magic', 'martial arts', 'mecha', 'military', 'music',
       'mystery', 'parody', 'police', 'psychological', 'romance', 'samurai',
       'school', 'sci-fi', 'seinen', 'shoujo', 'shoujo ai', 'shounen',
       'shounen ai', 'slice of life', 'space', 'sports', 'super power',
       'supernatural', 'thriller', 'vampire', 'yaoi', 'yuri'],
      dtype='object')

In [144]:
# df_item_feature.columns[2:-1].shape

**Coba hitung user_feature_vector untuk 4 User --> menjadi user_feature_matrix**

In [145]:
list_user_feature_vector = []

for user in range(len(df_user_items)):

    # buat item feature matix with rating
    df_item_feature_rating = df_item_feature.loc[list(df_user_items.columns[1:]), 'action':'yuri'].multiply(df_user_items.iloc[user, 1:], axis=0)


    # buat user feature vector
    user_feature_vector = df_item_feature_rating.sum() / df_item_feature_rating.sum().sum()
    list_user_feature_vector.append(user_feature_vector.values)

# buat dataframe user_feature_matrix (kumpulan dari user_feature_vector)
user_feature_matrix = pd.DataFrame(list_user_feature_vector, columns=df_item_feature_rating.columns, index=df_user_items['user'])
user_feature_matrix   

action  adventure  cars    comedy  dementia  demons  drama  ecchi  \
user                                                                          
user 1  0.105263   0.120301   0.0  0.157895       0.0     0.0    0.0    0.0   
user 2  0.111888   0.104895   0.0  0.146853       0.0     0.0    0.0    0.0   
user 3  0.104478   0.134328   0.0  0.149254       0.0     0.0    0.0    0.0   
user 4  0.105263   0.105263   0.0  0.157895       0.0     0.0    0.0    0.0   

        fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
user                                                                           
user 1      0.0   0.0    0.0     0.0    0.037594     0.0    0.0   0.0    0.0   
user 2      0.0   0.0    0.0     0.0    0.062937     0.0    0.0   0.0    0.0   
user 3      0.0   0.0    0.0     0.0    0.037313     0.0    0.0   0.0    0.0   
user 4      0.0   0.0    0.0     0.0    0.052632     0.0    0.0   0.0    0.0   

        martial arts  mecha  military  music   mystery    parody    police  \
user                                                                         
user 1           0.0    0.0       0.0    0.0  0.052632  0.037594  0.052632   
user 2           0.0    0.0       0.0    0.0  0.055944  0.062937  0.055944   
user 3           0.0    0.0       0.0    0.0  0.067164  0.037313  0.067164   
user 4           0.0    0.0       0.0    0.0  0.052632  0.052632  0.052632   

        psychological  romance   samurai  school    sci-fi  seinen    shoujo  \
user                                                                           
user 1            0.0      0.0  0.037594     0.0  0.037594     0.0  0.067669   
user 2            0.0      0.0  0.062937     0.0  0.062937     0.0  0.027972   
user 3            0.0      0.0  0.037313     0.0  0.037313     0.0  0.044776   
user 4            0.0      0.0  0.052632     0.0  0.052632     0.0  0.052632   

        shoujo ai   shounen  shounen ai  slice of life  space  sports  \
user                                                                    
user 1        0.0  0.157895         0.0       0.067669    0.0     0.0   
user 2        0.0  0.167832         0.0       0.027972    0.0     0.0   
user 3        0.0  0.171642         0.0       0.044776    0.0     0.0   
user 4        0.0  0.157895         0.0       0.052632    0.0     0.0   

        super power  supernatural  thriller  vampire  yaoi  yuri  
user                                                              
user 1     0.067669           0.0       0.0      0.0   0.0   0.0  
user 2     0.048951           0.0       0.0      0.0   0.0   0.0  
user 3     0.067164           0.0       0.0      0.0   0.0   0.0  
user 4     0.052632           0.0       0.0      0.0   0.0   0.0

In [146]:
user_feature_matrix.shape

(4, 43)

## Filter dataframe without 4 chosen anime

Ini adalah anime-anime yang belum pernah ditonton oleh 4 user tersebut. 

In [147]:
# df_user_items

In [148]:
# Anime yang belum ditonton
df_item_feature_new = df_genre.loc[~df_genre['anime_id'].isin(df_user_items.columns[1:])]
df_item_feature_new

anime_id                                               name  action  \
0         32281                                     Kimi no Na wa.       0   
1          5114                   Fullmetal Alchemist: Brotherhood       1   
2         28977                                           Gintama°       1   
3          9253                                        Steins;Gate       0   
4          9969                                      Gintama&#039;       1   
...         ...                                                ...     ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami       0   
12013      5543                                        Under World       0   
12014      5621                     Violence Gekiga David no Hoshi       0   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...       0   
12016     26081                   Yasuji no Pornorama: Yacchimae!!       0   

       adventure  cars  comedy  dementia  demons  drama  ecchi  fantasy  game  \
0              0     0       0         0       0      1      0        0     0   
1              1     0       0         0       0      1      0        1     0   
2              0     0       1         0       0      0      0        0     0   
3              0     0       0         0       0      0      0        0     0   
4              0     0       1         0       0      0      0        0     0   
...          ...   ...     ...       ...     ...    ...    ...      ...   ...   
12012          0     0       0         0       0      0      0        0     0   
12013          0     0       0         0       0      0      0        0     0   
12014          0     0       0         0       0      0      0        0     0   
12015          0     0       0         0       0      0      0        0     0   
12016          0     0       0         0       0      0      0        0     0   

       harem  hentai  historical  horror  josei  kids  magic  martial arts  \
0          0       0           0       0      0     0      0             0   
1          0       0           0       0      0     0      1             0   
2          0       0           1       0      0     0      0             0   
3          0       0           0       0      0     0      0             0   
4          0       0           1       0      0     0      0             0   
...      ...     ...         ...     ...    ...   ...    ...           ...   
12012      0       1           0       0      0     0      0             0   
12013      0       1           0       0      0     0      0             0   
12014      0       1           0       0      0     0      0             0   
12015      0       1           0       0      0     0      0             0   
12016      0       1           0       0      0     0      0             0   

       mecha  military  music  mystery  parody  police  psychological  \
0          0         0      0        0       0       0              0   
1          0         1      0        0       0       0              0   
2          0         0      0        0       1       0              0   
3          0         0      0        0       0       0              0   
4          0         0      0        0       1       0              0   
...      ...       ...    ...      ...     ...     ...            ...   
12012      0         0      0        0       0       0              0   
12013      0         0      0        0       0       0              0   
12014      0         0      0        0       0       0              0   
12015      0         0      0        0       0       0              0   
12016      0         0      0        0       0       0              0   

       romance  samurai  school  sci-fi  seinen  shoujo  shoujo ai  shounen  \
0            1        0       1       0       0       0          0        0   
1            0        0       0       0       0       0          0        1   
2            0        1       0       1       

## Create predicted score for unwatched anime

Mengalikan nilai pada User Fature Vector (preferensi tiap user) dengan anime yang belum ditonton

In [149]:
user_feature_matrix

action  adventure  cars    comedy  dementia  demons  drama  ecchi  \
user                                                                          
user 1  0.105263   0.120301   0.0  0.157895       0.0     0.0    0.0    0.0   
user 2  0.111888   0.104895   0.0  0.146853       0.0     0.0    0.0    0.0   
user 3  0.104478   0.134328   0.0  0.149254       0.0     0.0    0.0    0.0   
user 4  0.105263   0.105263   0.0  0.157895       0.0     0.0    0.0    0.0   

        fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
user                                                                           
user 1      0.0   0.0    0.0     0.0    0.037594     0.0    0.0   0.0    0.0   
user 2      0.0   0.0    0.0     0.0    0.062937     0.0    0.0   0.0    0.0   
user 3      0.0   0.0    0.0     0.0    0.037313     0.0    0.0   0.0    0.0   
user 4      0.0   0.0    0.0     0.0    0.052632     0.0    0.0   0.0    0.0   

        martial arts  mecha  military  music   mystery    parody    police  \
user                                                                         
user 1           0.0    0.0       0.0    0.0  0.052632  0.037594  0.052632   
user 2           0.0    0.0       0.0    0.0  0.055944  0.062937  0.055944   
user 3           0.0    0.0       0.0    0.0  0.067164  0.037313  0.067164   
user 4           0.0    0.0       0.0    0.0  0.052632  0.052632  0.052632   

        psychological  romance   samurai  school    sci-fi  seinen    shoujo  \
user                                                                           
user 1            0.0      0.0  0.037594     0.0  0.037594     0.0  0.067669   
user 2            0.0      0.0  0.062937     0.0  0.062937     0.0  0.027972   
user 3            0.0      0.0  0.037313     0.0  0.037313     0.0  0.044776   
user 4            0.0      0.0  0.052632     0.0  0.052632     0.0  0.052632   

        shoujo ai   shounen  shounen ai  slice of life  space  sports  \
user                                                                    
user 1        0.0  0.157895         0.0       0.067669    0.0     0.0   
user 2        0.0  0.167832         0.0       0.027972    0.0     0.0   
user 3        0.0  0.171642         0.0       0.044776    0.0     0.0   
user 4        0.0  0.157895         0.0       0.052632    0.0     0.0   

        super power  supernatural  thriller  vampire  yaoi  yuri  
user                                                              
user 1     0.067669           0.0       0.0      0.0   0.0   0.0  
user 2     0.048951           0.0       0.0      0.0   0.0   0.0  
user 3     0.067164           0.0       0.0      0.0   0.0   0.0  
user 4     0.052632           0.0       0.0      0.0   0.0   0.0

In [150]:
df_item_feature_new

anime_id                                               name  action  \
0         32281                                     Kimi no Na wa.       0   
1          5114                   Fullmetal Alchemist: Brotherhood       1   
2         28977                                           Gintama°       1   
3          9253                                        Steins;Gate       0   
4          9969                                      Gintama&#039;       1   
...         ...                                                ...     ...   
12012      9316       Toushindai My Lover: Minami tai Mecha-Minami       0   
12013      5543                                        Under World       0   
12014      5621                     Violence Gekiga David no Hoshi       0   
12015      6133  Violence Gekiga Shin David no Hoshi: Inma Dens...       0   
12016     26081                   Yasuji no Pornorama: Yacchimae!!       0   

       adventure  cars  comedy  dementia  demons  drama  ecchi  fantasy  game  \
0              0     0       0         0       0      1      0        0     0   
1              1     0       0         0       0      1      0        1     0   
2              0     0       1         0       0      0      0        0     0   
3              0     0       0         0       0      0      0        0     0   
4              0     0       1         0       0      0      0        0     0   
...          ...   ...     ...       ...     ...    ...    ...      ...   ...   
12012          0     0       0         0       0      0      0        0     0   
12013          0     0       0         0       0      0      0        0     0   
12014          0     0       0         0       0      0      0        0     0   
12015          0     0       0         0       0      0      0        0     0   
12016          0     0       0         0       0      0      0        0     0   

       harem  hentai  historical  horror  josei  kids  magic  martial arts  \
0          0       0           0       0      0     0      0             0   
1          0       0           0       0      0     0      1             0   
2          0       0           1       0      0     0      0             0   
3          0       0           0       0      0     0      0             0   
4          0       0           1       0      0     0      0             0   
...      ...     ...         ...     ...    ...   ...    ...           ...   
12012      0       1           0       0      0     0      0             0   
12013      0       1           0       0      0     0      0             0   
12014      0       1           0       0      0     0      0             0   
12015      0       1           0       0      0     0      0             0   
12016      0       1           0       0      0     0      0             0   

       mecha  military  music  mystery  parody  police  psychological  \
0          0         0      0        0       0       0              0   
1          0         1      0        0       0       0              0   
2          0         0      0        0       1       0              0   
3          0         0      0        0       0       0              0   
4          0         0      0        0       1       0              0   
...      ...       ...    ...      ...     ...     ...            ...   
12012      0         0      0        0       0       0              0   
12013      0         0      0        0       0       0              0   
12014      0         0      0        0       0       0              0   
12015      0         0      0        0       0       0              0   
12016      0         0      0        0       0       0              0   

       romance  samurai  school  sci-fi  seinen  shoujo  shoujo ai  shounen  \
0            1        0       1       0       0       0          0        0   
1            0        0       0       0       0       0          0        1   
2            0        1       0       1       

In [151]:
user_feature_matrix.loc['user 1']

action           0.105263
adventure        0.120301
cars             0.000000
comedy           0.157895
dementia         0.000000
demons           0.000000
drama            0.000000
ecchi            0.000000
fantasy          0.000000
game             0.000000
harem            0.000000
hentai           0.000000
historical       0.037594
horror           0.000000
josei            0.000000
kids             0.000000
magic            0.000000
martial arts     0.000000
mecha            0.000000
military         0.000000
music            0.000000
mystery          0.052632
parody           0.037594
police           0.052632
psychological    0.000000
romance          0.000000
samurai          0.037594
school           0.000000
sci-fi           0.037594
seinen           0.000000
shoujo           0.067669
shoujo ai        0.000000
shounen          0.157895
shounen ai       0.000000
slice of life    0.067669
space            0.000000
sports           0.000000
super power      0.067669
supernatural

In [152]:
df_item_feature_new.drop(columns=['anime_id', 'name'])

action  adventure  cars  comedy  dementia  demons  drama  ecchi  \
0           0          0     0       0         0       0      1      0   
1           1          1     0       0         0       0      1      0   
2           1          0     0       1         0       0      0      0   
3           0          0     0       0         0       0      0      0   
4           1          0     0       1         0       0      0      0   
...       ...        ...   ...     ...       ...     ...    ...    ...   
12012       0          0     0       0         0       0      0      0   
12013       0          0     0       0         0       0      0      0   
12014       0          0     0       0         0       0      0      0   
12015       0          0     0       0         0       0      0      0   
12016       0          0     0       0         0       0      0      0   

       fantasy  game  harem  hentai  historical  horror  josei  kids  magic  \
0            0     0      0       0           0       0      0     0      0   
1            1     0      0       0           0       0      0     0      1   
2            0     0      0       0           1       0      0     0      0   
3            0     0      0       0           0       0      0     0      0   
4            0     0      0       0           1       0      0     0      0   
...        ...   ...    ...     ...         ...     ...    ...   ...    ...   
12012        0     0      0       1           0       0      0     0      0   
12013        0     0      0       1           0       0      0     0      0   
12014        0     0      0       1           0       0      0     0      0   
12015        0     0      0       1           0       0      0     0      0   
12016        0     0      0       1           0       0      0     0      0   

       martial arts  mecha  military  music  mystery  parody  police  \
0                 0      0         0      0        0       0       0   
1                 0      0         1      0        0       0       0   
2                 0      0         0      0        0       1       0   
3                 0      0         0      0        0       0       0   
4                 0      0         0      0        0       1       0   
...             ...    ...       ...    ...      ...     ...     ...   
12012             0      0         0      0        0       0       0   
12013             0      0         0      0        0       0       0   
12014             0      0         0      0        0       0       0   
12015             0      0         0      0        0       0       0   
12016             0      0         0      0        0       0       0   

       psychological  romance  samurai  school  sci-fi  seinen  shoujo  \
0                  0        1        0       1       0       0       0   
1                  0        0        0       0       0       0       0   
2                  0        0        1       0       1       0       0   
3                  0        0        0       0       1       0       0   
4                  0        0        1       0       1       0       0   
...              ...      ...      ...     ...     ...     ...     ...   
12012              0        0        0       0       0       0       0   
12013              0        0        0       0       0       0       0   
12014              0        0        0       0       0       0       0   
12015              0        0        0       0       0       0       0   
12016              0        0        0       0       0       0       0   

       shoujo ai  shounen  shounen ai  slice of life  space  sports  \
0              0        0           0              0      0       0   
1              0        1           0              0      0       0   
2              0        1           0              0      0       0   
3              0        0           0              0      0       0   
4              0        1           0              0      0 

In [153]:
list_movie_score = []

for user in range(len(user_feature_matrix)):

    # movie score
    movie_score = df_item_feature_new.drop(columns=['anime_id', 'name']).mul(user_feature_matrix.iloc[user]).sum(axis=1)
    list_movie_score.append(movie_score.values)

# Score yang diberikan oleh masing-masing user untuk tiap film
user_item_matix = pd.DataFrame(list_movie_score, columns=df_item_feature_new['name'].values, index=user_feature_matrix.index)
user_item_matix

Kimi no Na wa.  Fullmetal Alchemist: Brotherhood  Gintama°  \
user                                                                 
user 1             0.0                          0.383459  0.571429   
user 2             0.0                          0.384615  0.678322   
user 3             0.0                          0.410448  0.574627   
user 4             0.0                          0.368421  0.631579   

        Steins;Gate  Gintama&#039;  \
user                                 
user 1     0.037594       0.571429   
user 2     0.062937       0.678322   
user 3     0.037313       0.574627   
user 4     0.052632       0.631579   

        Haikyuu!!: Karasuno Koukou VS Shiratorizawa Gakuen Koukou  \
user                                                                
user 1                                           0.315789           
user 2                                           0.314685           
user 3                                           0.320896           
user 4                                           0.315789           

        Hunter x Hunter (2011)  Ginga Eiyuu Densetsu  \
user                                                   
user 1                0.451128              0.037594   
user 2                0.433566              0.062937   
user 3                0.477612              0.037313   
user 4                0.421053              0.052632   

        Gintama Movie: Kanketsu-hen - Yorozuya yo Eien Nare  \
user                                                          
user 1                                           0.571429     
user 2                                           0.678322     
user 3                                           0.574627     
user 4                                           0.631579     

        Gintama&#039;: Enchousen  Clannad: After Story  Koe no Katachi  \
user                                                                     
user 1                  0.571429              0.067669        0.157895   
user 2                  0.678322              0.027972        0.167832   
user 3                  0.574627              0.044776        0.171642   
user 4                  0.631579              0.052632        0.157895   

        Code Geass: Hangyaku no Lelouch R2  Haikyuu!! Second Season  \
user                                                                  
user 1                            0.210526                 0.315789   
user 2                            0.223776                 0.314685   
user 3                            0.208955                 0.320896   
user 4                            0.210526                 0.315789   

        Sen to Chihiro no Kamikakushi  Shigatsu wa Kimi no Uso  \
user                                                             
user 1                       0.120301                 0.157895   
user 2                       0.104895                 0.167832   
user 3                       0.134328                 0.171642   
user 4                       0.105263                 0.157895   

        Mushishi Zoku Shou 2nd Season  Ookami Kodomo no Ame to Yuki  \
user                                                                  
user 1                       0.278195                      0.067669   
user 2                       0.251748                      0.027972   
user 3                       0.283582                      0.044776   
user 4                       0.263158                      0.052632   

        Code Geass: Hangyaku no Lelouch  Hajime no Ippo  \
user                                                      
user 1                         0.210526        0.315789   
user 2                         0.223776        0.314685   
user 3                         0.208955        0.320896   
user 4                         0.210526        0.315789   

        Rurouni Kenshin: Meiji Kenkaku Romantan - Tsuioku-hen  Cowboy Bebop  \
user                                                                          
user 1            

## Recommendation for User 1-4

In [154]:
df_user_items

user  951  136  235  918
0  user 1    9    9    7    5
1  user 2    4    7    8    9
2  user 3    6    9    9    5
3  user 4    7    7    7    7

In [155]:
df_item_feature

name  action  adventure  cars  comedy  dementia  \
anime_id                                                                 
951       Chibi Maruko-chan       0          0     0       1         0   
136         Hunter x Hunter       1          1     0       0         0   
235         Detective Conan       0          1     0       1         0   
918                 Gintama       1          0     0       1         0   

          demons  drama  ecchi  fantasy  game  harem  hentai  historical  \
anime_id                                                                   
951            0      0      0        0     0      0       0           0   
136            0      0      0        0     0      0       0           0   
235            0      0      0        0     0      0       0           0   
918            0      0      0        0     0      0       0           1   

          horror  josei  kids  magic  martial arts  mecha  military  music  \
anime_id                                                                     
951            0      0     0      0             0      0         0      0   
136            0      0     0      0             0      0         0      0   
235            0      0     0      0             0      0         0      0   
918            0      0     0      0             0      0         0      0   

          mystery  parody  police  psychological  romance  samurai  school  \
anime_id                                                                     
951             0       0       0              0        0        0       0   
136             0       0       0              0        0        0       0   
235             1       0       1              0        0        0       0   
918             0       1       0              0        0        1       0   

          sci-fi  seinen  shoujo  shoujo ai  shounen  shounen ai  \
anime_id                                                           
951            0       0       1          0        0           0   
136            0       0       0          0        1           0   
235            0       0       0          0        1           0   
918            1       0       0          0        1           0   

          slice of life  space  sports  super power  supernatural  thriller  \
anime_id                                                                      
951                   1      0       0            0             0         0   
136                   0      0       0            1             0         0   
235                   0      0       0            0             0         0   
918                   0      0       0            0             0         0   

          vampire  yaoi  yuri  
anime_id                       
951             0     0     0  
136             0     0     0  
235             0     0     0  
918             0     0     0

### User 1

Memberi rating besar pada Chibi Maruko-chan dan Hunter x Hunter

In [156]:
user_item_matix.T[['user 1']].sort_values('user 1', ascending=False).head(10) 

user                                                  user 1
Dragon Ball Z: Zenbu Misemasu Toshi Wasure Drag...  0.676692
Tenkai Knights                                      0.646617
Dragon Ball Movie 4: Saikyou e no Michi             0.646617
Dragon Ball: Episode of Bardock                     0.646617
Dragon Ball Movie 3: Makafushigi Daibouken          0.646617
Dragon Ball GT                                      0.646617
Dragon Ball Movie 2: Majinjou no Nemuri Hime        0.646617
Chiisana Kyojin Microman                            0.646617
Burn Up Excess                                      0.631579
Betterman                                           0.631579

### User 2

Memberi rating besar pada Detective Conan dan Gintama

In [157]:
user_item_matix.T[['user 2']].sort_values('user 2', ascending=False).head(10)

user                                                  user 2
Gintama Movie: Kanketsu-hen - Yorozuya yo Eien ...  0.678322
Gintama Movie: Shinyaku Benizakura-hen              0.678322
Gintama: Shinyaku Benizakura-hen                    0.678322
Gintama: Yorinuki Gintama-san on Theater 2D         0.678322
Gintama: Jump Festa 2014 Special                    0.678322
Gintama&#039;: Enchousen                            0.678322
Gintama: Nanigoto mo Saiyo ga Kanjin nano de Ta...  0.678322
Gintama&#039;                                       0.678322
Gintama°                                            0.678322
Dokkoida                                            0.657343

### User 3

Memberi rating besar pada Hunter x Hunter dan Detective Conan 

In [158]:
user_item_matix.T[['user 3']].sort_values('user 3', ascending=False).head(10)

user                                                  user 3
Dragon Ball Z: Zenbu Misemasu Toshi Wasure Drag...  0.671642
Betterman                                           0.664179
Burn Up Excess                                      0.664179
Bomberman Jetters                                   0.664179
Dragon Ball Movie 2: Majinjou no Nemuri Hime        0.664179
Chiisana Kyojin Microman                            0.664179
Dragon Ball Movie 3: Makafushigi Daibouken          0.664179
Dragon Ball Movie 4: Saikyou e no Michi             0.664179
Dragon Ball GT                                      0.664179
Dragon Ball: Episode of Bardock                     0.664179

### User 4

Memberi rating yang sama (7) pada 'Chibi Maruko-chan', 'Hunter x Hunter', 'Detective Conan', 'Gintama'

In [159]:
user_item_matix.T[['user 4']].sort_values('user 4', ascending=False).head(10)

user                                                  user 4
Dokkoida                                            0.631579
Tenkai Knights                                      0.631579
Dragon Ball Z: Zenbu Misemasu Toshi Wasure Drag...  0.631579
Bomberman Jetters                                   0.631579
Gintama Movie: Shinyaku Benizakura-hen              0.631579
Dragon Ball: Episode of Bardock                     0.631579
Dragon Ball Movie 4: Saikyou e no Michi             0.631579
Gintama: Shinyaku Benizakura-hen                    0.631579
Burn Up Excess                                      0.631579
Betterman                                           0.631579